# Age

In [27]:
import geopandas as gpd
import pandas as pd
import numpy as np
import geopandas as gpd
from shapely.geometry import Point
import folium
from libpysal import graph

In [28]:
cd /home/lisa/work/people_places_germany/code

/home/lisa/work/people_places_germany/code


In [29]:
from spatial_autocorrelation import lisa
from clusters import assign_clusters

In [30]:
clusters = gpd.read_parquet('/data/cluster_data/clusters_umap_freiburg_100_3_gaussian_euclidean_complete_chebyshev_3.pq')

In [31]:
#clusters.explore(column=clusters.index,cmap='tab20')

# Raw Data

In [32]:
demographics = pd.read_parquet('/data/processed_data/Bevoelkerung100M.parquet').reset_index()

In [33]:
gdf, largest_overlap, data = assign_clusters(demographics,clusters)

/home/lisa/work/people_places_germany/code/clusters.py:25: UserWarning: `keep_geom_type=True` in overlay resulted in 2 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  overlap = gpd.overlay(cells, clusters, how='intersection')


In [34]:
#calculate average age
age = data['AGE_10']

gdf['STATS','Average Age'] = ((age['Under 10'].fillna(0)*5 + age['10 - 19'].fillna(0)*15 + age['20 - 29'].fillna(0)*25 
                               + age['30 - 39'].fillna(0)*35 + age['40 - 49'].fillna(0)*45 + age['50 - 59'].fillna(0)*55 
                               + age['60 - 69'].fillna(0)*65 + age['70 - 79'].fillna(0)*75 + age['80 and older'].fillna(0)*85) 
                               / age[['Under 10', '20 - 29', '60 - 69', '10 - 19','40 - 49', '50 - 59','30 - 39', '70 - 79',
                                      '80 and older']].sum(axis=1))

In [35]:
gdf1 = gdf[['ID','geometry','cluster','STATS']]
gdf1.columns = gdf1.columns.get_level_values(0)

In [36]:
gdf2 = gdf[['ID','AGE_10']]
gdf2.columns = gdf2.columns.get_level_values(1)
gdf1 = gdf1.merge(gdf2, how='left', on='ID')

# Compute Spatial Lag

In [37]:
gdf1 = gdf1.cx[4150000:4170000,2760000:2780000]

In [38]:
gdf1 = gdf1[gdf1.cluster.notna()]
queen = graph.Graph.build_contiguity(gdf1, rook=False)
row_wise_queen = queen.transform("R")

In [39]:
gdf1.columns

Index(['ID', 'geometry', 'cluster', 'STATS', 'Under 10', '20 - 29', '60 - 69',
       '10 - 19', '40 - 49', '50 - 59', '30 - 39', '70 - 79', '80 and older'],
      dtype='object')

In [40]:
for i in ['STATS','Under 10', '20 - 29', '60 - 69','10 - 19', '40 - 49', '50 - 59', '30 - 39', '70 - 79', '80 and older']:
    gdf1.loc[:,i+'_lag']=row_wise_queen.lag(gdf1[i])

In [41]:
gdf1.to_parquet('/home/lisa/work/people_places_germany/Notebooks/temp_data/age.parquet')

In [42]:
gdf1.columns

Index(['ID', 'geometry', 'cluster', 'STATS', 'Under 10', '20 - 29', '60 - 69',
       '10 - 19', '40 - 49', '50 - 59', '30 - 39', '70 - 79', '80 and older',
       'STATS_lag', 'Under 10_lag', '20 - 29_lag', '60 - 69_lag',
       '10 - 19_lag', '40 - 49_lag', '50 - 59_lag', '30 - 39_lag',
       '70 - 79_lag', '80 and older_lag'],
      dtype='object')

In [43]:
gdf1

ID                                           geometry  \
135761  100mN27618E41614  POLYGON ((4161500 2761900, 4161500 2761800, 41...   
136068  100mN27619E41614  POLYGON ((4161500 2762000, 4161500 2761900, 41...   
137524  100mN27624E41613  POLYGON ((4161400 2762500, 4161400 2762400, 41...   
137825  100mN27625E41613  POLYGON ((4161400 2762600, 4161400 2762500, 41...   
137826  100mN27625E41614  POLYGON ((4161500 2762600, 4161500 2762500, 41...   
...                  ...                                                ...   
167939  100mN27712E41616  POLYGON ((4161700 2771300, 4161700 2771200, 41...   
168243  100mN27713E41610  POLYGON ((4161100 2771400, 4161100 2771300, 41...   
168244  100mN27713E41611  POLYGON ((4161200 2771400, 4161200 2771300, 41...   
168567  100mN27714E41609  POLYGON ((4161000 2771500, 4161000 2771400, 41...   
168568  100mN27714E41610  POLYGON ((4161100 2771500, 4161100 2771400, 41...   

        cluster      STATS  Under 10  20 - 29  60 - 69  10 - 19  40 - 49  \
135761      1.0  51.666667       NaN      3.0      NaN      NaN      3.0   
136068      1.0        NaN       NaN      NaN      NaN      NaN      NaN   
137524     14.0  56.600000       NaN      3.0      4.0      NaN      4.0   
137825     14.0  45.666667       4.0     14.0      9.0      5.0     10.0   
137826     14.0  45.000000       NaN      NaN      NaN      NaN      3.0   
...         ...        ...       ...      ...      ...      ...      ...   
167939     16.0        NaN       NaN      NaN      NaN      NaN      NaN   
168243     14.0  15.000000       NaN      NaN      NaN      3.0      NaN   
168244     14.0  33.571429       NaN      4.0      NaN      3.0      NaN   
168567     14.0        NaN       NaN      NaN      NaN      NaN      NaN   
168568     14.0  22.142857       4.0      NaN      NaN      NaN      3.0   

        50 - 59  ...  STATS_lag  Under 10_lag  20 - 29_lag  60 - 69_lag  \
135761      NaN  ...        NaN           NaN          NaN          NaN   
136068      NaN  ...  51.666667           NaN     3.000000          NaN   
137524      3.0  ...  45.333333           NaN          NaN          NaN   
137825      9.0  ...  46.606780           NaN          NaN          NaN   
137826      NaN  ...  46.829002           NaN     9.333333     5.666667   
...         ...  ...        ...           ...          ...          ...   
167939      NaN  ...  38.333333           NaN     3.000000          NaN   
168243      NaN  ...        NaN           NaN          NaN          NaN   
168244      4.0  ...  18.571429           NaN          NaN          NaN   
168567      NaN  ...  18.571429           NaN          NaN          NaN   
168568      NaN  ...        NaN           NaN          NaN          NaN   

        10 - 19_lag  40 - 49_lag  50 - 59_lag  30 - 39_lag  70 - 79_lag  \
135761          NaN          NaN          NaN          NaN          NaN   
136068          NaN     3.000000          NaN          NaN          NaN   
137524          NaN     6.500000          NaN          NaN          NaN   
137825          NaN     5.000000          NaN          NaN          NaN   
137826          NaN     7.333333     5.666667    12.333333     5.666667   
...             ...          ...          ...          ...          ...   
167939          NaN          NaN     3.000000     3.000000          NaN   
168243          NaN          NaN          NaN          NaN          NaN   
168244          NaN          NaN          NaN          NaN          NaN   
168567          NaN          NaN          NaN          NaN          NaN   
168568          NaN          NaN          NaN          NaN          NaN   

        80 and older_lag  
135761               NaN  
136068               3.0  
137524               NaN  
137825               NaN  
137826               NaN  
...                  ...  
167939               NaN  
168243               NaN  
168244               NaN  
168567               NaN  
168568               NaN  

[2514 rows x 23 columns]

In [44]:
#gdf1.explore("STATS", cmap="coolwarm", prefer_canvas=True)

# Local Spatial Autocorrelation

In [45]:
mi, gdf_05 = lisa(gdf1,'STATS',0.05)

('WARNING: ', 135761, ' is an island (no neighbors)')
('WARNING: ', 144394, ' is an island (no neighbors)')
('WARNING: ', 147893, ' is an island (no neighbors)')
('WARNING: ', 147894, ' is an island (no neighbors)')
('WARNING: ', 148278, ' is an island (no neighbors)')
('WARNING: ', 151300, ' is an island (no neighbors)')
('WARNING: ', 151701, ' is an island (no neighbors)')
('WARNING: ', 152171, ' is an island (no neighbors)')
('WARNING: ', 152173, ' is an island (no neighbors)')
('WARNING: ', 152494, ' is an island (no neighbors)')
('WARNING: ', 152545, ' is an island (no neighbors)')
('WARNING: ', 152890, ' is an island (no neighbors)')
('WARNING: ', 158308, ' is an island (no neighbors)')
('WARNING: ', 161267, ' is an island (no neighbors)')
('WARNING: ', 162306, ' is an island (no neighbors)')
('WARNING: ', 164427, ' is an island (no neighbors)')
('WARNING: ', 165836, ' is an island (no neighbors)')
('WARNING: ', 166478, ' is an island (no neighbors)')
('WARNING: ', 167063, ' is a

/opt/conda/lib/python3.11/site-packages/libpysal/graph/base.py:267: UserWarning: The weights matrix is not fully connected: 
 There are 42 disconnected components.
 There are 20 islands with ids: 135761, 144394, 147893, 147894, 148278, 151300, 151701, 152171, 152173, 152494, 152545, 152890, 158308, 161267, 162306, 164427, 165836, 166478, 167063, 167645.
  return W(neighbors=neighbors, weights=weights, id_order=self.unique_ids)
/opt/conda/lib/python3.11/site-packages/esda/moran.py:1059: RuntimeWarning: invalid value encountered in divide
  self.z_sim = (self.Is - self.EI_sim) / self.seI_sim


In [46]:
print(f"Moran's I: {mi.I}, p-value: {mi.p_sim}")

Moran's I: 0.21631754684460897, p-value: 0.001


In [47]:
#gdf_05.explore("sig_cluster", prefer_canvas=True, cmap=["#d7191c","#fdae61","#abd9e9","#2c7bb6","lightgrey"])

# Cluster Aggregation

In [48]:
gdf

Variable                ID  INSGESAMT    AGE_5                       \
Category                ID      Total Under 18 30 - 49 65 and older   
0         100mN26891E43370        8.0      3.0     3.0          3.0   
1         100mN26891E43411        7.0      3.0     3.0          NaN   
2         100mN26908E43412        3.0      NaN     NaN          NaN   
3         100mN26912E43412       10.0      4.0     3.0          3.0   
4         100mN26917E43411       10.0      3.0     NaN          3.0   
...                    ...        ...      ...     ...          ...   
3177718   100mN35476E42198        8.0      NaN     3.0          4.0   
3177719   100mN35476E42199       18.0      NaN     5.0          6.0   
3177720   100mN35476E42200       10.0      NaN     9.0          NaN   
3177721   100mN35476E42201        8.0      NaN     NaN          5.0   
3177722   100mN35508E42187        4.0      NaN     3.0          NaN   

Variable MARITAL_STATUS         COUNTRY_OF_BIRTH              GENDER  ...  \
Category         Single Married          Germany EU27 country   Male  ...   
0                   4.0     3.0              6.0          3.0    4.0  ...   
1                   4.0     3.0              7.0          NaN    4.0  ...   
2                   NaN     3.0              3.0          NaN    NaN  ...   
3                   6.0     4.0             10.0          NaN    6.0  ...   
4                   4.0     3.0             10.0          NaN    4.0  ...   
...                 ...     ...              ...          ...    ...  ...   
3177718             3.0     6.0              8.0          NaN    4.0  ...   
3177719             8.0     7.0             15.0          NaN    5.0  ...   
3177720             5.0     3.0             10.0          NaN    8.0  ...   
3177721             NaN     5.0              6.0          NaN    5.0  ...   
3177722             NaN     3.0              4.0          NaN    3.0  ...   

Variable NATIONALITY_COUNTRY NATIONALITY_NO NATIONALITY_GROUP  \
Category  Russian Federation      Not known             Other   
0                        NaN            NaN               NaN   
1                        NaN            NaN               NaN   
2                        NaN            NaN               NaN   
3                        NaN            NaN               NaN   
4                        NaN            NaN               NaN   
...                      ...            ...               ...   
3177718                  NaN            NaN               NaN   
3177719                  NaN            NaN               NaN   
3177720                  NaN            NaN               NaN   
3177721                  NaN            NaN               NaN   
3177722                  NaN            NaN               NaN   

Variable NATIONALITY_COUNTRY MARITAL_STATUS  \
Category          Kazakhstan No information   
0                        NaN            NaN   
1                        NaN            NaN   
2                        NaN            NaN   
3                        NaN            NaN   
4                        NaN            NaN   
...                      ...            ...   
3177718                  NaN            NaN   
3177719                  NaN            NaN   
3177720                  NaN            NaN   
3177721                  NaN            NaN   
3177722                  NaN            NaN   

Variable                                         \
Category Registered Civil partnership dissolved   
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   
...                                         ...   
3177718                                     NaN   
3177719                                     NaN   
3177720                                     NaN   
3177721                                     NaN   
3177

In [49]:
d = []
for i in range(0,int(data['cluster','cluster'].max())):
    d.append(
        {
            'Average age': gdf[gdf['cluster','cluster']==i]['STATS','Average Age'].mean(),
            'Average age count': gdf[gdf['cluster','cluster']==i]['STATS','Average Age'].count()
        }
    )

stats = pd.DataFrame(d)

In [50]:
stats['label']=stats.index
stats = clusters.merge(stats,on='label')

In [51]:
#stats.explore(column='Average age', cmap="coolwarm", prefer_canvas=True,vmax=50)

In [53]:
m = stats.explore(column='Average age', cmap="coolwarm", prefer_canvas=True, name = "cluster aggregation")

gdf_05.explore("sig_cluster", prefer_canvas=True, cmap=["#d7191c","#fdae61","#abd9e9","#2c7bb6","lightgrey"],name = "local spatial autocorrelation",m=m)

gdf1.cx[4150000:4170000,2760000:2780000].explore("STATS", cmap="coolwarm", prefer_canvas=True, name = "raw data", m=m)

# Add a layer control to toggle the layers on and off
folium.LayerControl().add_to(m)

# Display the map
m